In [7]:
import glob
songs = glob.glob('midifiles/**/*.mid', recursive=True)

In [4]:
from music21 import converter

file = converter.parse('midifiles/Butterfly.mid')
components = []
for element in file.recurse():
    components.append(element)
components

[<music21.stream.Part 0x7fe8cd7b7790>,
 <music21.instrument.Piano Piano>,
 <music21.tempo.MetronomeMark Quarter=75.0>,
 <music21.key.Key of D- major>,
 <music21.meter.TimeSignature 4/4>,
 <music21.stream.Voice 0x7fe8cdc05690>,
 <music21.note.Note C#>,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note C#>,
 <music21.note.Note C#>,
 <music21.note.Note E->,
 <music21.note.Note C#>,
 <music21.note.Note C#>,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note C#>,
 <music21.note.Note F>,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note F>,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note E->,
 <music21.note.Note C#>,
 <music21.note.Note E->,
 <music21.note.Note C#>,
 <music21.note.Note F>,
 <music21.note.Note C#>,
 

In [5]:
import pickle
from music21 import instrument, note, chord, stream

In [8]:
notes = []

for file in songs:
    midi = converter.parse(file)
    notes_to_parse = []

    try:
        parts = instrument.partitionByInstrument(midi)
    except:
        pass

    if parts:
        notes_to_parse = parts.parts[0].recurse()
    else:
        notes_to_parse = midi.flat.notes

    for element in notes_to_parse:
        if isinstance(element, note.Note):
            notes.append(str(element.pitch))

        elif isinstance(element, chord.Chord):
            notes.append(".".join(str(n) for n in element.normalOrder))

with open("notes", "wb") as filepath:
    pickle.dump(notes, filepath)

In [9]:
import numpy as np
from tensorflow.keras import utils

In [11]:
seq_length = 100

pitchnames = sorted(set(notes))
n_vocab = len(set(notes))
notes_to_int = dict((pitch, n) for n, pitch in enumerate(pitchnames))

net_in = []
net_out = []

for i in range(0, len(notes) - seq_length, 1):
    seq_in = notes[i : i + seq_length]
    seq_out = notes[i + seq_length]
    net_in.append([notes_to_int[j] for j in seq_in])
    net_out.append(notes_to_int[seq_out])

number_of_patterns = len(net_in)

net_in = np.reshape(net_in, (number_of_patterns, seq_length, 1))
net_in = net_in / float(len(pitchnames))
net_out = utils.to_categorical(net_out)

In [13]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import (
    Activation, LSTM, Dense, Dropout, Flatten, BatchNormalization
)

In [15]:
from tensorflow.keras.optimizers import Adam

model = Sequential()
model.add(LSTM(256, return_sequences=True, input_shape=net_in.shape[1:]))
model.add(Dropout(0.3))
model.add(BatchNormalization())
model.add(LSTM(512, return_sequences=True))
model.add(Dropout(0.3))
model.add(BatchNormalization())
model.add(LSTM(256))
model.add(BatchNormalization())
model.add(Dense(256))
model.add(Dropout(0.3))
model.add(Dense(n_vocab))
model.add(Activation("softmax"))
model.compile(loss="categorical_crossentropy", optimizer='rmsprop')

In [16]:
from tensorflow.keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, EarlyStopping

es_callback = EarlyStopping(monitor="loss", min_delta=0, patience=6)
reduce_lr = ReduceLROnPlateau(monitor='loss', factor=0.1, patience=3, verbose=1)
filepath = 'ep{epoch:03d}-loss{loss:.2f}.h5'
checkpoint = ModelCheckpoint(
    filepath, monitor="loss", verbose=0, save_best_only=True, save_weights_only=True, 
    period=3
)
model.fit(net_in, net_out, epochs=100, batch_size=64, callbacks=[checkpoint, es_callback, reduce_lr],)

Epoch 1/100
158/158 [==============================] - 38s 137ms/step - loss: 4.5471 - lr: 0.0010
Epoch 2/100
158/158 [==============================] - 22s 137ms/step - loss: 3.8225 - lr: 0.0010
Epoch 3/100
158/158 [==============================] - 22s 137ms/step - loss: 3.5391 - lr: 0.0010
Epoch 4/100
158/158 [==============================] - 22s 137ms/step - loss: 3.2694 - lr: 0.0010
Epoch 5/100
158/158 [==============================] - 22s 137ms/step - loss: 2.9884 - lr: 0.0010
Epoch 6/100
158/158 [==============================] - 22s 137ms/step - loss: 2.7328 - lr: 0.0010
Epoch 7/100
158/158 [==============================] - 22s 137ms/step - loss: 2.5305 - lr: 0.0010
Epoch 8/100
158/158 [==============================] - 22s 137ms/step - loss: 2.3729 - lr: 0.0010
Epoch 9/100
158/158 [==============================] - 21s 136ms/step - loss: 2.2275 - lr: 0.0010
Epoch 10/100
158/158 [==============================] - 21s 136ms/step - loss: 2.1183 - lr: 0.0010
Epoch 11/100
158/15

In [17]:
model.load_weights('ep099-loss0.05.h5')

In [29]:
note_to_int = dict((pitch, number) for number, pitch in enumerate(pitchnames))

sequence_length = 100
network_input = []

for i in range(0, len(notes) - sequence_length, 1):
    sequence_in = notes[i : i + sequence_length]
    network_input.append([note_to_int[char] for char in sequence_in])

normalized_in = np.reshape(network_input, (len(network_input), 100, 1))
normalized_in = normalized_in / float(n_vocab)

In [35]:
start = np.random.randint(0, len(net_in) - 1)
int_to_note = dict((number, note) for number, note in enumerate(pitchnames))
pattern = net_in[start]
prediction_output = []
print("Generating notes")

for note_index in range(500):
    prediction_input = np.reshape(pattern, (1, len(pattern), 1))
    prediction_input = prediction_input / float(n_vocab)
    prediction = model.predict(prediction_input, verbose=0)

    index = np.argmax(prediction)
    result = int_to_note[index]
    prediction_output.append(result)

    pattern.append(index)
    pattern = pattern[1 : len(pattern)]
print("Notes generated")

Generating notes
Notes generated


In [36]:
offset = 0
output_notes = []

for pattern in prediction_output:
    if ("." in pattern) or pattern.isdigit():
        notes_in_chord = pattern.split(".")
        notes = []

        for current_note in notes_in_chord:
            new_note = note.Note(int(current_note))
            new_note.storedInstrument = instrument.Piano()
            notes.append(new_note)

        new_chord = chord.Chord(notes)
        new_chord.offset = offset
        output_notes.append(new_chord)

    else:
        new_note = note.Note(pattern)
        new_note.offset = offset
        new_note.storedInstrument = instrument.Piano()
        output_notes.append(new_note)

    offset += 0.5

midi_stream = stream.Stream(output_notes)
midi_stream.write("midi", fp="output.mid")

'output.mid'

In [40]:
!apt-get install timidity

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  freepats libaudio2 timidity-daemon
Suggested packages:
  nas fluid-soundfont-gs pmidi
The following NEW packages will be installed:
  freepats libaudio2 timidity timidity-daemon
0 upgraded, 4 newly installed, 0 to remove and 37 not upgraded.
Need to get 29.6 MB of archives.
After this operation, 35.7 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 freepats all 20060219-1 [29.0 MB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/main amd64 libaudio2 amd64 1.9.4-6 [50.3 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/universe amd64 timidity amd64 2.13.2-41 [585 kB]
Get:4 http://archive.ubuntu.com/ubuntu bionic/universe amd64 timidity-daemon all 2.13.2-41 [5,984 B]
Fetched 29.6 MB in 2s (12.8 MB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is

In [43]:
!timidity output.mid -Ow -o - | ffmpeg -i - -acodec libmp3lame -ab 320k output.mp3

Playing output.mid
MIDI file: output.mid
Format: 1  Tracks: 1  Divisions: 1024
Sequence: 
ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-l

In [44]:
import IPython
IPython.display.Audio("output.mp3")